In [654]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import numpy as np

Diabetes Dataset - Данные о заболеваемости диабетом среди женщин не моложе 21 года, родом из индейцев Пима.

1. Pregnancies: количество беременностей
2. Glucose: концентрация глюкозы в плазме через 2 часа при пероральном тесте на толерантность к глюкозе.
3. BloodPressure: Диастолическое артериальное давление (мм рт. ст.)
4. SkinThickness: Толщина кожной складки трицепса (мм).
5. Insulin: 2-часовой сывороточный инсулин (мю Ед/мл)
6. BMI: индекс массы тела (вес в кг/(рост в м)^2)
7. DiabetesPedigreeFunction: показатель возможности развития диабета на основании семейного анамнеза
8. Age: Возраст (лет)
9. Outcome: переменная класса (0 или 1).

In [655]:
diabetes_data = pd.read_csv('data/diabetes.csv')
display(diabetes_data.head())

Pregnancies  Glucose  BloodPressure  SkinThickness  Insulin   BMI  \
0            6      148             72             35        0  33.6   
1            1       85             66             29        0  26.6   
2            8      183             64              0        0  23.3   
3            1       89             66             23       94  28.1   
4            0      137             40             35      168  43.1   

   DiabetesPedigreeFunction  Age  Outcome  
0                     0.627   50        1  
1                     0.351   31        0  
2                     0.672   32        1  
3                     0.167   21        0  
4                     2.288   33        1

***Oхарактеризуйте имеющиеся колонки и число наблюдений. Проанализируйте, какие факторы связаны с развитием диабета, а какие нет.***

In [656]:
diabetes_data.shape

(768, 9)

In [657]:
# Анализируем датасет на наличие пропущенных данных 
def nan_function(x):
    return np.nan if x == 0 else x
diabetes_data["Glucose"] = diabetes_data["Glucose"].apply(nan_function)
diabetes_data["BloodPressure"] = diabetes_data["BloodPressure"].apply(nan_function)
diabetes_data["SkinThickness"] = diabetes_data["SkinThickness"].apply(nan_function)
diabetes_data["Insulin"] = diabetes_data["Insulin"].apply(nan_function)
diabetes_data["BMI"] = diabetes_data["BMI"].apply(nan_function)
diabetes_data.isnull().mean().round(2).sort_values(ascending=False)

Insulin                     0.49
SkinThickness               0.30
BloodPressure               0.05
Glucose                     0.01
BMI                         0.01
Pregnancies                 0.00
DiabetesPedigreeFunction    0.00
Age                         0.00
Outcome                     0.00
dtype: float64

In [658]:
# Удаляем из данных признаки, где число пропусков составляет более 30%
n = diabetes_data.shape[0] #число строк в таблице
thresh = n*0.7
diabetes_cleaned = diabetes_data.dropna(thresh=thresh, axis=1)

diabetes_cleaned.shape

(768, 8)

In [659]:
# Удаляем из данных строки, в которых содержится более двух пропусков одновременно
m = diabetes_cleaned.shape[1] #число признаков после удаления столбцов
diabetes_cleaned = diabetes_cleaned.dropna(thresh=m-2, axis=0)

diabetes_cleaned.shape

(761, 8)

In [660]:
# В оставшихся записях заменяем пропуски на медиану
values = {
    'Glucose': diabetes_cleaned['Glucose'].median(),
    'BloodPressure': diabetes_cleaned['BloodPressure'].median(),
    'SkinThickness': diabetes_cleaned['SkinThickness'].median(),
    'BMI': diabetes_cleaned['BMI'].median(),
}
#заполняем оставшиеся записи константами в соответствии со словарем values
diabetes_cleaned = diabetes_cleaned.fillna(values)

***Вывод:*** 

_Датасет после очистки данных содержит 761 запись_

По статистике 2 из 5 женщин репродуктивного возраста страдают сахарным диабетом. 

Гипотеза: в данной выборке будет около 40% больных диабетом

In [661]:
labels = ['Healthy','Diabetic'] # легенда
values = diabetes_cleaned['Outcome'].value_counts() # данные для диаграммы
colors = ['seagreen','LightCoral'] # цветовая гамма

# строим график и отображаем его
fig = go.Figure(data=[go.Pie(labels=labels, values=values, marker=dict(colors=colors))])
fig.show()

***Вывод:*** 

_В данной выборке доля пациентов, больных диабетом, составляет 35.1%_

Cахарный диабет может возникнуть в любом возрасте, но чаще всего встречается после 40 лет

Гипотеза: в данной выборке медианный возраст будет около 40 лет

In [662]:
# проводим фильтрацию данных
mask = diabetes_cleaned['Outcome'] == 1

# строим график и отображаем его
fig = px.box(
    diabetes_cleaned[mask], # датафрейм
    x="Age", # ось x
    points="all"
)
fig.update_layout(
    title_text='Распределение возраста больных', # заголовок
    xaxis_title_text='Возраст', # ось x
)
fig.show()

***Вывод:*** 

_Медианный возраст среди больных в данной выборке составляет 36 лет. Основное количество пациенток в возрасте от 28 до 44 лет_

Aртериальная гипертензия является одним из факторов риска развития сахарного диабета 2-го типа и в сочетании с избыточной массой тела, нарушением липидного обмена, нарушением толерантности к углеводам может привести в 40 % случаев к этому заболеванию и в дальнейшем значительно повысить количество сердечно-сосудистых и почечных осложнений

Гипотеза: между уровнем глюкозы, полученным в тесте на толерантность к глюкозе, и показателем диастолического давления есть корреляция

In [663]:
# строим график и отображаем его
fig = px.scatter(
    diabetes_cleaned, # датафрейм
    x="Glucose", # ось x
    y="BloodPressure", # ось y
    color="Outcome"
)
fig.update_layout(
    title_text='Взаимосвязь уровня глюкозы и показателем давления', # заголовок
    xaxis_title_text='Уровень глюкозы ', # ось x
    yaxis_title_text='Показатель давления', # ось y
)
fig.show()

***Вывод:*** 

_Распределения больных диабетом и здоровых пациенток выглядят примерно одинаково_

Bысокий индекс массы тела ассоциирован с повышением риска сахарного диабета 2 типа

Гипотеза: среди пациентов с повышенным ИМТ большинство болеют диабетом

In [664]:
# проводим фильтрацию данных 
bar_data = diabetes_cleaned[diabetes_cleaned['BMI'] > 30].groupby( 
    by ='Outcome',
    as_index=False
).count()

# строим график и отображаем его
fig = px.bar(
    data_frame=bar_data, # датафрейм
    x="Outcome", # ось x
    y="BMI", # ось y
    color='Outcome', # цветовая гамма
    orientation='v', # ориентация графика
    height=500, # высота
    width=1000, # ширина
    title='Распределение пациентов, страдающих ожирением',
    color_discrete_sequence=['#330C73','#EB89B5']# цветовая гамма
)
fig.update_layout(
    xaxis_title_text='Наличие диабета', # ось x
    yaxis_title_text='Количество пациентов', # ось y
)
fig.show()

***Вывод:*** 

_В данной выборке среди пациентов, страдающих ожирением, преобладают люди без сахарного диабета_

Согласно литературным данным, в 20-25% случаев гестационный диабет может развиться в сахарный диабет

Гипотеза: с большим числом беременностей увеличивается вероятность выявления диабета 

In [665]:
# проводим фильтрацию данных 
mask1=diabetes_cleaned[diabetes_cleaned['Outcome'] == 1]['Pregnancies']
mask2=diabetes_cleaned[diabetes_cleaned['Outcome'] == 0]['Pregnancies']

# строим график
fig = go.Figure()
# гистограмма для диaгностированных больных
fig.add_trace(go.Histogram(
    x=mask1, # выбираем только диaгностированных больных
    name='Diabetic', # легенда
    xbins=dict( # столбцы гистограммы 
        start=0.0,
        end=100.0,
        size=1
    ),
    marker_color='#EB89B5', # цветовая гамма
    opacity=0.75 # прозрачность
))
# гистограмма для здоровых людей
fig.add_trace(go.Histogram(
    x=mask2, # выбираем здоровых людей
    name='Healthy', # легенда
    xbins=dict( # столбцы гистограммы 
        start=0.0,
        end=100.0,
        size=1
    ),
    marker_color='#330C73', # цветовая гамма
    opacity=0.75 # прозрачность
))
fig.update_layout(
    title_text='Распределение пациентов', # заголовок
    xaxis_title_text='Количество беременностей', # ось x
    yaxis_title_text='Количество пациентов', # ось y 
    bargap=0.2, # отступы между группами столбцов 
    bargroupgap=0.1 # отступы между столбцами в группе
)
# отображаем график
fig.show()

***Вывод:*** 

_Среди пациенток с количеством беременностей до 7 преобладают пациентки без диабета. Среди пациенток с 7 и более беременностями вероятность сахарного диабета составляет 50% и более_

Tолщина кожи определяется содержанием коллагена и увеличивается при инсулинозависимом сахарном диабете

Гипотеза: у диабетиков толщина кожной складки выше, чем у здоровых людей 

In [666]:
# проводим фильтрацию данных согласно условию
mask1=diabetes_data[diabetes_data['Outcome'] == 1]['SkinThickness']
mask2=diabetes_data[diabetes_data['Outcome'] == 0]['SkinThickness']

# строим график
fig = go.Figure()
# гистограмма для диaгностированных больных
fig.add_trace(go.Histogram(
    x=mask1, # выбираем только диaгностированных больных
    name='Diabetic', # легенда
    xbins=dict( # столбцы гистограммы 
        start=0.0,
        end=150.0,
        size=10
    ),
    marker_color='#EB89B5', # цветовая гамма
    opacity=0.75 # прозрачность
))
# гистограмма для здоровых людей
fig.add_trace(go.Histogram(
    x=mask2, # выбираем здоровых людей
    name='Healthy', # легенда
    xbins=dict( # столбцы гистограммы 
        start=0.0,
        end=150.0,
        size=10
    ),
    marker_color='#330C73', # цветовая гамма
    opacity=0.75 # прозрачность
))
fig.update_layout(
    title_text='Распределение пациентов', # заголовок
    xaxis_title_text='Толщина кожи', # ось x
    yaxis_title_text='Количество пациентов', # ось y 
    bargap=0.2, # отступы между группами столбцов 
    bargroupgap=0.1 # отступы между столбцами в группе
)
# отображаем график
fig.show()

***Вывод:*** 

_У пациенток с диабетом в среднем более высокие значения толщины кожной складки_

Рассмотрим взаимосвязь возраста и ИМТ с диабетом

In [667]:
# Функция для перевода числового признака Age в категориальный
def get_age_cat(age):
        if age >= 21 and age < 30:
            return "20+"
        elif age >= 30 and age < 40:
            return "30+"
        elif age >= 40 and age < 50:
            return "40+"
        elif age >= 50 and age < 60:
            return "50+"
        elif age >= 60 and age < 70:
            return "60+"
        elif age >= 70 and age < 80:
            return "70+"
        elif age >= 80 and age < 90:
            return "80+"    
        elif age > 90:
            return "90+"
        
# Переводим числовой признак в категориальный        
diabetes_cleaned['AgeCat']=diabetes_cleaned['Age'].apply(get_age_cat)   

# Создаем сводную таблицу
pivot = diabetes_cleaned.pivot_table(
    values='Outcome',
    columns='BMI',
    index='AgeCat'
)

# Функция, которая переводит формат Pandas DataFrame в поддерживаемый Plotly формат
def pivot_to_plotly(df):
    return {
        'z': df.values.tolist(),
        'x': df.columns.tolist(),
        'y': df.index.tolist()     
    }

# строим график и отображаем его  
fig = go.Figure(
    data=go.Heatmap(pivot_to_plotly(pivot))
)
fig.update_layout(
    title_text='Взаимосвязь возраста и ИМТ с диабетом', # заголовок
    xaxis_title_text='BMI', # ось x
    yaxis_title_text='Возрастная категория', # ось y
)
fig.show() 

***Вывод:*** 

_С увеличением возраста и ИМТ чаще встречается диабет_

In [668]:
# показатель возможности развития диабета на основании семейного анамнеза (чем выше, тем выше шанс наследственной заболеваемости)

# проводим фильтрацию данных согласно условию
mask1=diabetes_cleaned[diabetes_cleaned['Outcome'] == 1]['DiabetesPedigreeFunction']
mask2=diabetes_cleaned[diabetes_cleaned['Outcome'] == 0]['DiabetesPedigreeFunction']

# строим график
fig = go.Figure()
# гистограмма для диaгностированных больных
fig.add_trace(go.Histogram(
    x=mask1, # выбираем только диaгностированных больных
    name='Diabetic', # легенда
    xbins=dict( # столбцы гистограммы 
        start=0.0,
        end=3.0,
        size=0.1
    ),
    marker_color='#EB89B5', # цветовая гамма
    opacity=0.75 # прозрачность
))
# гистограмма для здоровых людей
fig.add_trace(go.Histogram(
    x=mask2, # выбираем здоровых людей
    name='Healthy', # легенда
    xbins=dict( # столбцы гистограммы 
        start=0.0,
        end=3.0,
        size=0.1
    ),
    marker_color='#330C73', # цветовая гамма
    opacity=0.75 # прозрачность
))
fig.update_layout(
    title_text='Распределение пациентов', # заголовок
    xaxis_title_text='DiabetesPedigreeFunction', # ось x
    yaxis_title_text='Количество пациентов', # ось y 
    bargap=0.2, # отступы между группами столбцов 
    bargroupgap=0.1 # отступы между столбцами в группе
)
# отображаем график
fig.show()

***Вывод:*** 

_Распределения больных диабетом и здоровых пациенток выглядят примерно одинаково_

***Вывод:*** 

_Датасет содержит 768 записей, из которых 7 записей содержали 2 и более пропусков и были удалены. Также из-за пропусков был удален столбец с показателями сывороточного инсулина_

_Все содержащиеся в таблице показатели либо являются факторами, связанными с развитием диабета, либо результатами анализов, выявляющих наличие диабета (концентрация глюкозы в крови  и сывороточный инсулин - результаты теста на толерантность к глюкозе)_




___
**Добавляем второй датасет**
___

Cardiovascular Study Dataset - Данные о наиболее важных факторах риска сердечно-сосудистых заболеваний.

1. Sex: мужской или женский ("M" или "F")
2. Age: Возраст пациента
3. is_smoking: является ли пациент курильщиком ("YES" или "NO")
4. Cigs Per Day: количество сигарет, которое человек выкуривает в среднем за один день
5. BP Meds: принимал ли пациент лекарства от артериального давления
6. Prevalent Stroke: перенес ли пациент ранее инсульт
7. Prevalent Hyp: была ли у пациента гипертензия
8. Diabetes: был ли у пациента диабет
9. Tot Chol: уровень общего холестерина 
10. Sys BP: систолическое артериальное давление
11. Dia BP: диастолическое артериальное давление 
12. BMI: индекс массы тела
13. Heart Rate: частота сердечных сокращений
14. Glucose: уровень глюкозы
15. 10 year risk of coronary heart disease CHD: 10-летний риск развития ишемической болезни сердца


In [669]:
cardio_data = pd.read_csv('data/train.csv')
display(cardio_data.head())

id  age  education sex is_smoking  cigsPerDay  BPMeds  prevalentStroke  \
0   0   64        2.0   F        YES         3.0     0.0                0   
1   1   36        4.0   M         NO         0.0     0.0                0   
2   2   46        1.0   F        YES        10.0     0.0                0   
3   3   50        1.0   M        YES        20.0     0.0                0   
4   4   64        1.0   F        YES        30.0     0.0                0   

   prevalentHyp  diabetes  totChol  sysBP  diaBP    BMI  heartRate  glucose  \
0             0         0    221.0  148.0   85.0    NaN       90.0     80.0   
1             1         0    212.0  168.0   98.0  29.77       72.0     75.0   
2             0         0    250.0  116.0   71.0  20.35       88.0     94.0   
3             1         0    233.0  158.0   88.0  28.26       68.0     94.0   
4             0         0    241.0  136.5   85.0  26.42       70.0     77.0   

   TenYearCHD  
0           1  
1           0  
2           0  
3           1  
4           0

In [670]:
cardio_data.shape

(3390, 17)

In [671]:
# Подготовка к объединению
diabetes_data['sex'] = 'F'
diabetes_data.rename(columns={'Glucose':'glucose', 'BloodPressure':'diaBP', 'Age':'age', 'Outcome':'diabetes'}, inplace=True)
diabetes_data

Pregnancies  glucose  diaBP  SkinThickness  Insulin   BMI  \
0              6    148.0   72.0           35.0      NaN  33.6   
1              1     85.0   66.0           29.0      NaN  26.6   
2              8    183.0   64.0            NaN      NaN  23.3   
3              1     89.0   66.0           23.0     94.0  28.1   
4              0    137.0   40.0           35.0    168.0  43.1   
..           ...      ...    ...            ...      ...   ...   
763           10    101.0   76.0           48.0    180.0  32.9   
764            2    122.0   70.0           27.0      NaN  36.8   
765            5    121.0   72.0           23.0    112.0  26.2   
766            1    126.0   60.0            NaN      NaN  30.1   
767            1     93.0   70.0           31.0      NaN  30.4   

     DiabetesPedigreeFunction  age  diabetes sex  
0                       0.627   50         1   F  
1                       0.351   31         0   F  
2                       0.672   32         1   F  
3                       0.167   21         0   F  
4                       2.288   33         1   F  
..                        ...  ...       ...  ..  
763                     0.171   63         0   F  
764                     0.340   27         0   F  
765                     0.245   30         0   F  
766                     0.349   47         1   F  
767                     0.315   23         0   F  

[768 rows x 10 columns]

In [672]:
# Соединяем датасеты
diabetes_cardio = pd.concat([cardio_data,diabetes_data], ignore_index=True) 
diabetes_cardio

id  age  education sex is_smoking  cigsPerDay  BPMeds  prevalentStroke  \
0     0.0   64        2.0   F        YES         3.0     0.0              0.0   
1     1.0   36        4.0   M         NO         0.0     0.0              0.0   
2     2.0   46        1.0   F        YES        10.0     0.0              0.0   
3     3.0   50        1.0   M        YES        20.0     0.0              0.0   
4     4.0   64        1.0   F        YES        30.0     0.0              0.0   
...   ...  ...        ...  ..        ...         ...     ...              ...   
4153  NaN   63        NaN   F        NaN         NaN     NaN              NaN   
4154  NaN   27        NaN   F        NaN         NaN     NaN              NaN   
4155  NaN   30        NaN   F        NaN         NaN     NaN              NaN   
4156  NaN   47        NaN   F        NaN         NaN     NaN              NaN   
4157  NaN   23        NaN   F        NaN         NaN     NaN              NaN   

      prevalentHyp  diabetes  ...  sysBP  diaBP    BMI  heartRate  glucose  \
0              0.0         0  ...  148.0   85.0    NaN       90.0     80.0   
1              1.0         0  ...  168.0   98.0  29.77       72.0     75.0   
2              0.0         0  ...  116.0   71.0  20.35       88.0     94.0   
3              1.0         0  ...  158.0   88.0  28.26       68.0     94.0   
4              0.0         0  ...  136.5   85.0  26.42       70.0     77.0   
...            ...       ...  ...    ...    ...    ...        ...      ...   
4153           NaN         0  ...    NaN   76.0  32.90        NaN    101.0   
4154           NaN         0  ...    NaN   70.0  36.80        NaN    122.0   
4155           NaN         0  ...    NaN   72.0  26.20        NaN    121.0   
4156           NaN         1  ...    NaN   60.0  30.10        NaN    126.0   
4157           NaN         0  ...    NaN   70.0  30.40        NaN     93.0   

      TenYearCHD  Pregnancies  SkinThickness  Insulin  \
0            1.0          NaN            NaN      NaN   
1            0.0          NaN            NaN      NaN   
2            0.0          NaN            NaN      NaN   
3            1.0          NaN            NaN      NaN   
4            0.0          NaN            NaN      NaN   
...          ...          ...            ...      ...   
4153         NaN         10.0           48.0    180.0   
4154         NaN          2.0           27.0      NaN   
4155         NaN          5.0           23.0    112.0   
4156         NaN          1.0            NaN      NaN   
4157         NaN          1.0           31.0      NaN   

      DiabetesPedigreeFunction  
0                          NaN  
1                          NaN  
2                          NaN  
3                          NaN  
4                          NaN  
...                        ...  
4153                     0.171  
4154                     0.340  
4155                     0.245  
4156                     0.349  
4157                     0.315  

[4158 rows x 21 columns]

In [673]:
diabetes_cardio.shape

(4158, 21)

In [674]:
#список неинформативных признаков
low_information_cols = [] 

#цикл по всем столбцам
for col in diabetes_cardio.columns:
    #наибольшая относительная частота в признаке
    top_freq = diabetes_cardio[col].value_counts(normalize=True).max()
    #доля уникальных значений от размера признака
    nunique_ratio = diabetes_cardio[col].nunique() / diabetes_cardio[col].count()
    # сравниваем наибольшую частоту с порогом
    if top_freq > 0.95:
        low_information_cols.append(col)
        print(f'{col}: {round(top_freq*100, 2)}% одинаковых значений')
    # сравниваем долю уникальных значений с порогом
    if nunique_ratio > 0.95:
        low_information_cols.append(col)
        print(f'{col}: {round(nunique_ratio*100, 2)}% уникальных значений')

id: 100.0% уникальных значений
BPMeds: 97.01% одинаковых значений
prevalentStroke: 99.35% одинаковых значений


In [675]:
diabetes_cardio = diabetes_cardio.drop(low_information_cols, axis=1)
print(f'Результирующее число признаков: {diabetes_cardio.shape[1]}')

Результирующее число признаков: 18


In [676]:
# Анализируем датасет на наличие пропущенных данных 
diabetes_cardio.isnull().mean().round(2).sort_values(ascending=False)

Insulin                     0.91
SkinThickness               0.87
DiabetesPedigreeFunction    0.82
Pregnancies                 0.82
education                   0.21
cigsPerDay                  0.19
totChol                     0.19
TenYearCHD                  0.18
is_smoking                  0.18
prevalentHyp                0.18
sysBP                       0.18
heartRate                   0.18
glucose                     0.07
diaBP                       0.01
BMI                         0.01
diabetes                    0.00
sex                         0.00
age                         0.00
dtype: float64

In [677]:
# Удаляем из данных признаки, где число пропусков составляет более 30%
n = diabetes_cardio.shape[0] #число строк в таблице
thresh = n*0.7
diabetes_cardio_cleaned = diabetes_cardio.dropna(thresh=thresh, axis=1)

diabetes_cardio_cleaned.shape

(4158, 14)

In [678]:
# В оставшихся записях заменяем пропуски на медиану
values = {
    'cigsPerDay': diabetes_cardio_cleaned['cigsPerDay'].median(),
    'totChol': diabetes_cardio_cleaned['totChol'].median(),
    'sysBP': diabetes_cardio_cleaned['sysBP'].median(),
    'heartRate': diabetes_cardio_cleaned['heartRate'].median(),
    'glucose': diabetes_cardio_cleaned['glucose'].median(),
    'diaBP': diabetes_cardio_cleaned['diaBP'].median(),
    'BMI': diabetes_cardio_cleaned['BMI'].median(),
}
#заполняем оставшиеся записи константами в соответствии со словарем values
diabetes_cardio_cleaned = diabetes_cardio_cleaned.fillna(values)

In [679]:
diabetes_cardio_cleaned.head()

age  education sex is_smoking  cigsPerDay  prevalentHyp  diabetes  totChol  \
0   64        2.0   F        YES         3.0           0.0         0    221.0   
1   36        4.0   M         NO         0.0           1.0         0    212.0   
2   46        1.0   F        YES        10.0           0.0         0    250.0   
3   50        1.0   M        YES        20.0           1.0         0    233.0   
4   64        1.0   F        YES        30.0           0.0         0    241.0   

   sysBP  diaBP    BMI  heartRate  glucose  TenYearCHD  
0  148.0   85.0  26.04       90.0     80.0         1.0  
1  168.0   98.0  29.77       72.0     75.0         0.0  
2  116.0   71.0  20.35       88.0     94.0         0.0  
3  158.0   88.0  28.26       68.0     94.0         1.0  
4  136.5   85.0  26.42       70.0     77.0         0.0

In [680]:
labels = ['Healthy','Diabetic'] # легенда
values = diabetes_cardio_cleaned['diabetes'].value_counts() # данные для диаграммы
colors = ['seagreen','LightCoral'] # цветовая гамма

# строим график и отображаем его
fig = go.Figure(data=[go.Pie(labels=labels, values=values, marker=dict(colors=colors))])
fig.show()

In [681]:
labels = ['Female','Male'] # легенда
values = diabetes_cardio_cleaned['sex'].value_counts() # данные для диаграммы
colors = ['seagreen','LightCoral'] # цветовая гамма

# строим график и отображаем его
fig = go.Figure(data=[go.Pie(labels=labels, values=values, marker=dict(colors=colors))])
fig.show()

In [682]:
labels = ['Smoker','Non-smoker'] # легенда
values = diabetes_cardio_cleaned['is_smoking'].value_counts() # данные для диаграммы
colors = ['seagreen','LightCoral'] # цветовая гамма

# строим график и отображаем его
fig = go.Figure(data=[go.Pie(labels=labels, values=values, marker=dict(colors=colors))])
fig.show()

***Вывод:*** 

_В данной выборке 8,5% больных диабетом, что превышает средние мировые показатели, половина - курящие, 2/3 наблюдений - женщины_

In [683]:
# проводим фильтрацию данных
mask = diabetes_cardio_cleaned['diabetes'] == 1

# строим график и отображаем его
fig = px.box(
    diabetes_cardio_cleaned[mask], # датафрейм
    x="age", # ось x
    points="all"
)
fig.update_layout(
    title_text='Распределение возраста больных', # заголовок
    xaxis_title_text='Возраст', # ось x
)
fig.show()

***Вывод:*** 

_Медианный возраст среди больных в данной выборке составляет 41 лет, что соответствует средним значениям по миру. Основное количество наблюдений в диапазоне от 30 до 52 лет_

Гипотеза: Люди с более высоким уровнем образования лучше следят за здоровьем и реже заболевают диабетом

In [684]:
# Группируем данные согласно условию
bar_data = diabetes_cardio_cleaned[diabetes_cardio_cleaned['diabetes']==1].groupby( 
    by ='education',
    as_index=False
).count()

# строим график и отображаем его
fig = px.bar(
    data_frame=bar_data, # датафрейм
    x="education", # ось x
    y="diabetes", # ось y
    color='education', # расцветка в зависимости от числа продуктов
    orientation='v', # ориентация графика
    height=500, # высота
    width=1000, # ширина
    title='Зависимость заболеваемости диабетом от уровня образования', #заголовок
    barmode='group'
)
fig.update_layout(
    xaxis_title_text='Уровень образования', # ось x
    yaxis_title_text='Количество наблюдений', # ось y
)
fig.show()

***Вывод:*** 

_Действительно, среди пациентов с диабетом преобладают люди с низким уровнем образования_

In [685]:
# проводим фильтрацию данных согласно условию
mask = diabetes_cardio_cleaned['diabetes'] == 1

# строим график
fig = px.histogram(
    data_frame=diabetes_cardio_cleaned[mask], # датафрейм
    x="cigsPerDay", # ось x
    nbins=35, # количество столбцов
    color_discrete_sequence=['#330C73'], # цветовая гамма
    orientation='v', # ориентация графика
    height=500, # высота
    width=1000, # ширина
    title='Распределение количества выкуриваемых сигарет в день ' # заголовок
)
# подписываем оси
fig.update_layout(
    xaxis_title_text='Количество выкуриваемых сигарет', # ось x
    yaxis_title_text='Количество наблюдений', # ось y 
)
# отображаем график
fig.show()

***Вывод:*** 

_Большинство диабетиков не курят, среди курящих большинство выкуривает около 1 пачки в день_

In [686]:
# Группируем данные 
bar_data = diabetes_cardio_cleaned[diabetes_cardio_cleaned['diabetes']==1].groupby( 
    by='prevalentHyp',
    as_index=False
).count()

# строим график и отображаем его
fig = px.bar(
    data_frame=bar_data, #датафрейм
    x="prevalentHyp", #ось x
    y="diabetes", #ось y
    color='prevalentHyp', #расцветка в зависимости от страны
    orientation='v', #ориентация графика
    height=500, #высота
    width=1000, #ширина
    barmode='group',
    title='Количество диагностированных больных с гипертензией среди диабетиков' #заголовок
)
fig.update_layout(
    xaxis_title_text='Статус пациента', # ось x
    yaxis_title_text='Количество пациентов', # ось y
)
fig.show()

***Вывод:*** 

_Гипертензия часто ассоциирована с сахарным диабетом_

Нормальное значение холестерола меньше 200 мг/дЛ

In [687]:
# проводим фильтрацию данных согласно условию
mask = diabetes_cardio_cleaned['diabetes'] == 1

# строим график
fig = px.histogram(
    data_frame=diabetes_cardio_cleaned[mask], # датафрейм
    x="totChol", # ось x
    nbins=25, # количество столбцов
    color_discrete_sequence=['#330C73'], # цветовая гамма
    orientation='v', # ориентация графика
    height=500, # высота
    width=1000, # ширина
    title='Распределение уровня холестерола в крови ' # заголовок
)
# подписываем оси
fig.update_layout(
    xaxis_title_text='Уровень холестерола в крови', # ось x
    yaxis_title_text='Количество наблюдений', # ось y 
)
# отображаем график
fig.show()

***Вывод:*** 

_У большинства пациентов уровень холестерола в крови повышен_

In [688]:
# строим график и отображаем его
fig = px.scatter(
    diabetes_cardio, # датафрейм
    x="totChol", # ось x
    y="diaBP", # ось y
    color="diabetes"
)
fig.update_layout(
    title_text='Взаимосвязь yровеня холестерола в крови', # заголовок
    xaxis_title_text='Уровень холестерола в крови', # ось x
    yaxis_title_text='Показатель давления', # ось y
)
fig.show()

***Вывод:*** 

_У больных диабетом чаще встречаются одновременно повышенные показатели давления и холестерола_

In [689]:
labels = ['Not in Risk','In Risk'] # легенда
mask1=diabetes_cardio_cleaned[diabetes_cardio_cleaned['diabetes'] == 1]['TenYearCHD']

values = mask1.value_counts() # данные для диаграммы
colors = ['seagreen','LightCoral'] # цветовая гамма

# строим график и отображаем его
fig = go.Figure(data=[go.Pie(labels=labels, values=values, marker=dict(colors=colors))])
fig.show()

In [690]:
labels = ['Not in Risk','In Risk'] # легенда
mask1=diabetes_cardio_cleaned[diabetes_cardio_cleaned['diabetes'] == 0]['TenYearCHD']

values = mask1.value_counts() # данные для диаграммы
colors = ['seagreen','LightCoral'] # цветовая гамма

# строим график и отображаем его
fig = go.Figure(data=[go.Pie(labels=labels, values=values, marker=dict(colors=colors))])
fig.show()

***Вывод:*** 

_Среди диабетиков риск развития ИБС в течение 10 лет намного выше, чем у людей без диабета_

___
**Добавляем третий датасет**
___

In [691]:
binary_data = pd.read_csv('data/diabetes_binary_health_indicators_BRFSS2015.csv')
display(binary_data.head())

Diabetes_binary  HighBP  HighChol  CholCheck   BMI  Smoker  Stroke  \
0              0.0     1.0       1.0        1.0  40.0     1.0     0.0   
1              0.0     0.0       0.0        0.0  25.0     1.0     0.0   
2              0.0     1.0       1.0        1.0  28.0     0.0     0.0   
3              0.0     1.0       0.0        1.0  27.0     0.0     0.0   
4              0.0     1.0       1.0        1.0  24.0     0.0     0.0   

   HeartDiseaseorAttack  PhysActivity  Fruits  ...  AnyHealthcare  \
0                   0.0           0.0     0.0  ...            1.0   
1                   0.0           1.0     0.0  ...            0.0   
2                   0.0           0.0     1.0  ...            1.0   
3                   0.0           1.0     1.0  ...            1.0   
4                   0.0           1.0     1.0  ...            1.0   

   NoDocbcCost  GenHlth  MentHlth  PhysHlth  DiffWalk  Sex   Age  Education  \
0          0.0      5.0      18.0      15.0       1.0  0.0   9.0        4.0   
1          1.0      3.0       0.0       0.0       0.0  0.0   7.0        6.0   
2          1.0      5.0      30.0      30.0       1.0  0.0   9.0        4.0   
3          0.0      2.0       0.0       0.0       0.0  0.0  11.0        3.0   
4          0.0      2.0       3.0       0.0       0.0  0.0  11.0        5.0   

   Income  
0     3.0  
1     1.0  
2     8.0  
3     6.0  
4     4.0  

[5 rows x 22 columns]

In [692]:
binary_data.shape

(253680, 22)

In [693]:
#список неинформативных признаков
low_information_cols = [] 

#цикл по всем столбцам
for col in binary_data.columns:
    #наибольшая относительная частота в признаке
    top_freq = binary_data[col].value_counts(normalize=True).max()
    #доля уникальных значений от размера признака
    nunique_ratio = binary_data[col].nunique() / binary_data[col].count()
    # сравниваем наибольшую частоту с порогом
    if top_freq > 0.95:
        low_information_cols.append(col)
        print(f'{col}: {round(top_freq*100, 2)}% одинаковых значений')
    # сравниваем долю уникальных значений с порогом
    if nunique_ratio > 0.95:
        low_information_cols.append(col)
        print(f'{col}: {round(nunique_ratio*100, 2)}% уникальных значений')

CholCheck: 96.27% одинаковых значений
Stroke: 95.94% одинаковых значений
AnyHealthcare: 95.11% одинаковых значений


In [694]:
binary_data = binary_data.drop(low_information_cols, axis=1)
print(f'Результирующее число признаков: {binary_data.shape[1]}')

Результирующее число признаков: 19


In [695]:
diabetes_cardio.head()

age  education sex is_smoking  cigsPerDay  prevalentHyp  diabetes  totChol  \
0   64        2.0   F        YES         3.0           0.0         0    221.0   
1   36        4.0   M         NO         0.0           1.0         0    212.0   
2   46        1.0   F        YES        10.0           0.0         0    250.0   
3   50        1.0   M        YES        20.0           1.0         0    233.0   
4   64        1.0   F        YES        30.0           0.0         0    241.0   

   sysBP  diaBP    BMI  heartRate  glucose  TenYearCHD  Pregnancies  \
0  148.0   85.0    NaN       90.0     80.0         1.0          NaN   
1  168.0   98.0  29.77       72.0     75.0         0.0          NaN   
2  116.0   71.0  20.35       88.0     94.0         0.0          NaN   
3  158.0   88.0  28.26       68.0     94.0         1.0          NaN   
4  136.5   85.0  26.42       70.0     77.0         0.0          NaN   

   SkinThickness  Insulin  DiabetesPedigreeFunction  
0            NaN      NaN                       NaN  
1            NaN      NaN                       NaN  
2            NaN      NaN                       NaN  
3            NaN      NaN                       NaN  
4            NaN      NaN                       NaN

In [696]:
binary_data.head()

Diabetes_binary  HighBP  HighChol   BMI  Smoker  HeartDiseaseorAttack  \
0              0.0     1.0       1.0  40.0     1.0                   0.0   
1              0.0     0.0       0.0  25.0     1.0                   0.0   
2              0.0     1.0       1.0  28.0     0.0                   0.0   
3              0.0     1.0       0.0  27.0     0.0                   0.0   
4              0.0     1.0       1.0  24.0     0.0                   0.0   

   PhysActivity  Fruits  Veggies  HvyAlcoholConsump  NoDocbcCost  GenHlth  \
0           0.0     0.0      1.0                0.0          0.0      5.0   
1           1.0     0.0      0.0                0.0          1.0      3.0   
2           0.0     1.0      0.0                0.0          1.0      5.0   
3           1.0     1.0      1.0                0.0          0.0      2.0   
4           1.0     1.0      1.0                0.0          0.0      2.0   

   MentHlth  PhysHlth  DiffWalk  Sex   Age  Education  Income  
0      18.0      15.0       1.0  0.0   9.0        4.0     3.0  
1       0.0       0.0       0.0  0.0   7.0        6.0     1.0  
2      30.0      30.0       1.0  0.0   9.0        4.0     8.0  
3       0.0       0.0       0.0  0.0  11.0        3.0     6.0  
4       3.0       0.0       0.0  0.0  11.0        5.0     4.0

Подготавливаем таблицы к объединению, оставляем признаки, которые есть в обеих таблицах. Признаки HighBP, HighChol, Age переводим в категориальные в соответствии с форматом binary_data. Признак Sex изменяем также в соответствии с форматом binary_data

In [697]:
diabetes_cardio = diabetes_cardio.drop(['education', 'cigsPerDay', 'sysBP', 'heartRate', 'glucose', 'TenYearCHD', 'Pregnancies', 'SkinThickness', 'Insulin', 'DiabetesPedigreeFunction'], axis=1)
diabetes_cardio.head()

age sex is_smoking  prevalentHyp  diabetes  totChol  diaBP    BMI
0   64   F        YES           0.0         0    221.0   85.0    NaN
1   36   M         NO           1.0         0    212.0   98.0  29.77
2   46   F        YES           0.0         0    250.0   71.0  20.35
3   50   M        YES           1.0         0    233.0   88.0  28.26
4   64   F        YES           0.0         0    241.0   85.0  26.42

In [698]:
binary_data = binary_data.drop(['PhysActivity',	'Fruits', 'Veggies', 'HvyAlcoholConsump', 'NoDocbcCost', 'GenHlth', 'MentHlth', 'PhysHlth', 'DiffWalk', 'Education', 'Income'], axis=1)
binary_data.head()

Diabetes_binary  HighBP  HighChol   BMI  Smoker  HeartDiseaseorAttack  Sex  \
0              0.0     1.0       1.0  40.0     1.0                   0.0  0.0   
1              0.0     0.0       0.0  25.0     1.0                   0.0  0.0   
2              0.0     1.0       1.0  28.0     0.0                   0.0  0.0   
3              0.0     1.0       0.0  27.0     0.0                   0.0  0.0   
4              0.0     1.0       1.0  24.0     0.0                   0.0  0.0   

    Age  
0   9.0  
1   7.0  
2   9.0  
3  11.0  
4  11.0

In [699]:
diabetes_cardio['sex'] = diabetes_cardio['sex'].apply(lambda x: 1 if x=='F' else 0)

# Функция для перевода числового признака Age в категориальный
def get_age_cat(age):
        if age >= 18 and age < 24:
            return 1
        elif age >= 25 and age < 30:
            return 2
        elif age >= 30 and age < 35:
            return 3
        elif age >= 35 and age < 40:
            return 4
        elif age >= 40 and age < 45:
            return 5
        elif age >= 45 and age < 50:
            return 6
        elif age >= 50 and age < 55:
            return 7   
        elif age >= 55 and age < 60:
            return 8
        elif age >= 60 and age < 65:
            return 9  
        elif age >= 65 and age < 70:
            return 10  
        elif age >= 70 and age < 75:
            return 11 
        elif age >= 75 and age < 80:
            return 12   
        elif age > 80:
            return 13
        
# Переводим числовой признак в категориальный        
diabetes_cardio['age']=diabetes_cardio['age'].apply(get_age_cat)   

diabetes_cardio['is_smoking'] = diabetes_cardio['is_smoking'].apply(lambda x: 1 if x=='YES' else 0)

diabetes_cardio['totChol'] = diabetes_cardio['totChol'].apply(lambda x: 1 if x >= 200 else 0)

diabetes_cardio['diaBP'] = diabetes_cardio['diaBP'].apply(lambda x: 1 if x >= 90 else 0)

diabetes_cardio.rename(columns={'age':'Age', 'sex':'Sex', 'is_smoking':'Smoker', 'prevalentHyp':'HeartDiseaseorAttack', 'diabetes':'Diabetes_binary', 'totChol':'HighChol', 'diaBP':'HighBP'}, inplace=True)
diabetes_cardio


Age  Sex  Smoker  HeartDiseaseorAttack  Diabetes_binary  HighChol  \
0     9.0    1       1                   0.0                0         1   
1     4.0    0       0                   1.0                0         1   
2     6.0    1       1                   0.0                0         1   
3     7.0    0       1                   1.0                0         1   
4     9.0    1       1                   0.0                0         1   
...   ...  ...     ...                   ...              ...       ...   
4153  9.0    1       0                   NaN                0         0   
4154  2.0    1       0                   NaN                0         0   
4155  3.0    1       0                   NaN                0         0   
4156  6.0    1       0                   NaN                1         0   
4157  1.0    1       0                   NaN                0         0   

      HighBP    BMI  
0          0    NaN  
1          1  29.77  
2          0  20.35  
3          0  28.26  
4          0  26.42  
...      ...    ...  
4153       0  32.90  
4154       0  36.80  
4155       0  26.20  
4156       0  30.10  
4157       0  30.40  

[4158 rows x 8 columns]

In [700]:
# Соединяем датасеты
diabetes_binary = pd.concat([diabetes_cardio,binary_data], ignore_index=True) 
diabetes_binary

Age  Sex  Smoker  HeartDiseaseorAttack  Diabetes_binary  HighChol  \
0        9.0  1.0     1.0                   0.0              0.0       1.0   
1        4.0  0.0     0.0                   1.0              0.0       1.0   
2        6.0  1.0     1.0                   0.0              0.0       1.0   
3        7.0  0.0     1.0                   1.0              0.0       1.0   
4        9.0  1.0     1.0                   0.0              0.0       1.0   
...      ...  ...     ...                   ...              ...       ...   
257833   5.0  1.0     0.0                   0.0              0.0       1.0   
257834  11.0  0.0     0.0                   0.0              1.0       1.0   
257835   2.0  0.0     0.0                   0.0              0.0       0.0   
257836   7.0  1.0     0.0                   0.0              0.0       0.0   
257837   9.0  0.0     0.0                   1.0              1.0       1.0   

        HighBP    BMI  
0          0.0    NaN  
1          1.0  29.77  
2          0.0  20.35  
3          0.0  28.26  
4          0.0  26.42  
...        ...    ...  
257833     1.0  45.00  
257834     1.0  18.00  
257835     0.0  28.00  
257836     1.0  23.00  
257837     1.0  25.00  

[257838 rows x 8 columns]

In [701]:
labels = ['Healthy','Diabetic'] # легенда
values = diabetes_binary['Diabetes_binary'].value_counts() # данные для диаграммы
colors = ['seagreen','LightCoral'] # цветовая гамма

# строим график и отображаем его
fig = go.Figure(data=[go.Pie(labels=labels, values=values, marker=dict(colors=colors))])
fig.show()

In [702]:
labels = ['Male','Female'] # легенда
values = diabetes_binary['Sex'].value_counts() # данные для диаграммы
colors = ['seagreen','LightCoral'] # цветовая гамма

# строим график и отображаем его
fig = go.Figure(data=[go.Pie(labels=labels, values=values, marker=dict(colors=colors))])
fig.show()

In [703]:
labels = ['Smoker','Non-smoker'] # легенда
values = diabetes_binary['Smoker'].value_counts() # данные для диаграммы
colors = ['seagreen','LightCoral'] # цветовая гамма

# строим график и отображаем его
fig = go.Figure(data=[go.Pie(labels=labels, values=values, marker=dict(colors=colors))])
fig.show()

***Вывод:*** 

_В данной выборке 13.8% больных диабетом, что превышает средние мировые показатели, больше половины - курящие и больше половины - мужчины_

In [704]:
# строим график
fig = px.histogram(
    data_frame=diabetes_binary['Age'], # датафрейм
    x="Age", # ось x
    nbins=25, # количество столбцов
    color_discrete_sequence=['#330C73'], # цветовая гамма
    orientation='v', # ориентация графика
    height=500, # высота
    width=1000, # ширина
    title='Распределение возрастов' # заголовок
)
# подписываем оси
fig.update_layout(
    xaxis_title_text='Возраст наблюдаемого', # ось x
    yaxis_title_text='Количество наблюдений', # ось y 
)
# отображаем график
fig.show()

***Вывод:*** 

_Большинство пациентов среднего и пожилого возраста_

In [705]:
# проводим фильтрацию данных
mask = diabetes_binary['Diabetes_binary'] == 1

# строим график и отображаем его
fig = px.box(
    diabetes_binary[mask], # датафрейм
    x="Age", # ось x
    points="all"
)
fig.update_layout(
    title_text='Распределение возраста больных', # заголовок
    xaxis_title_text='Возраст', # ось x
)
fig.show()

***Вывод:*** 

_Диабет чаще выявляют у людей среднего и пожилого возраста_

In [706]:
# проводим фильтрацию данных 
bar_data = diabetes_binary[diabetes_binary['BMI'] > 30].groupby( 
    by ='Diabetes_binary',
    as_index=False
).count()

# строим график и отображаем его
fig = px.bar(
    data_frame=bar_data, # датафрейм
    x="Diabetes_binary", # ось x
    y="BMI", # ось y
    color='Diabetes_binary', # цветовая гамма
    orientation='v', # ориентация графика
    height=500, # высота
    width=1000, # ширина
    title='Распределение пациентов, страдающих ожирением',
    color_discrete_sequence=['#330C73','#EB89B5']# цветовая гамма
)
fig.update_layout(
    xaxis_title_text='Наличие диабета', # ось x
    yaxis_title_text='Количество пациентов', # ось y
)
fig.show()

***Вывод:*** 

_В данной выборке среди пациентов, страдающих ожирением, преобладают люди без сахарного диабета_

In [707]:
# Группируем данные 
bar_data = diabetes_binary[diabetes_binary['Diabetes_binary']==1].groupby( 
    by='HeartDiseaseorAttack',
    as_index=False
).count()

# строим график и отображаем его
fig = px.bar(
    data_frame=bar_data, #датафрейм
    x="HeartDiseaseorAttack", #ось x
    y="Diabetes_binary", #ось y
    color='HeartDiseaseorAttack', #расцветка в зависимости от страны
    orientation='v', #ориентация графика
    height=500, #высота
    width=1000, #ширина
    barmode='group',
    title='Количество диагностированных больных с сердечными заболеваниями среди диабетиков' #заголовок
)
fig.update_layout(
    xaxis_title_text='Статус пациента', # ось x
    yaxis_title_text='Количество пациентов', # ось y
)
fig.show()

***Вывод:*** 

_У большинства пациентов с сахарным диабетом в данной выборке не диагностированы сердечные заболевания_

In [708]:
# проводим фильтрацию данных согласно условию
bar_data = diabetes_binary[diabetes_binary['Diabetes_binary']==1].groupby( 
    by='HighChol',
    as_index=False
).count()

# строим график
fig = px.bar(
    data_frame=bar_data, #датафрейм
    x="HighChol", #ось x
    y="Diabetes_binary", #ось y
    color='HighChol', #расцветка в зависимости от страны
    orientation='v', #ориентация графика
    height=500, #высота
    width=1000, #ширина
    barmode='group',
    title='Распределение уровня холестерола в крови' #заголовок
)

# подписываем оси
fig.update_layout(
    xaxis_title_text='Статус пациента', # ось x
    yaxis_title_text='Количество пациентов', # ось y
)
# отображаем график
fig.show()

***Вывод:*** 

_У большинства пациентов с сахарным диабетом в данной выборке повышен уровень холестерола в крови_

In [711]:
fig = px.treemap(diabetes_binary, path=[px.Constant("all"), 'Diabetes_binary', 'HighChol', 'HighBP'], values='HighBP')
fig.update_traces(root_color="lightgrey")
fig.update_layout(margin = dict(t=50, l=25, r=25, b=25))
fig.show()

***Вывод:*** 

_В данной выборке большую часть составляют пациенты без диабета. Среди пациентов с диабетом у большинства повышен уровень холестерола. В обеих группах наблюдается большое число пациентов с повышенным давлением_